In [4]:
import pandas as pd 
import math
import plotly.express as px


In [6]:
sensex_1980 = "../data/SnP-Sensex-1980.csv"
sensex_df = pd.read_csv(sensex_1980, header=0)
sensex_df
del sensex_df["Low"]
del sensex_df["Open"]
del sensex_df["High"]
sensex_df["Returns"] = sensex_df["Close"].pct_change()
sensex_df= sensex_df.fillna(0)

In [8]:
sensex_df

Month     Close   Returns
0      January-1991    982.32  0.000000
1     February-1991   1220.41  0.242375
2        March-1991   1167.97 -0.042969
3        April-1991   1235.11  0.057484
4          May-1991   1307.34  0.058481
..              ...       ...       ...
353       June-2020  34915.80  0.076847
354       July-2020  37606.89  0.077074
355     August-2020  38628.29  0.027160
356  September-2020  38067.93 -0.014506
357    October-2020  40509.49  0.064137

[358 rows x 3 columns]

#### Effective Return = Return On Equity + Return on Debt - Inflated Value fo Withdrawl

In [121]:
DEBT_RETURN = 1.07
INFLATION_ANNUAL = 1.05
SWR = 7
monthly_debt_return = math.pow(DEBT_RETURN, 1/12) - 1
monthly_inflation = math.pow(INFLATION_ANNUAL, 1/12) - 1
initial_withdrawal = SWR/12
equity_share = .7
debt_share = 1 - equity_share
inital_portfolio_size = 100

In [122]:
withdrawals = list()
withdrawals_values = initial_withdrawal
for i in range(len(sensex_df.index)):
    withdrawals_values = (1+monthly_inflation)*withdrawals_values
    withdrawals.append(withdrawals_values)


In [123]:
# def portfolio_growth(inital_portfolio_size, equity_share, debt_share, withdrawals):
# equity = inital_portfolio_size*equity_share
# debt = inital_portfolio_size*debt_share
# current_month_amount = equity + debt
# monthly_portfolio_value = list()
# monthly_portfolio_value.append(current_month_amount)
# for index, row in sensex_df.iterrows():
#     if debt >= withdrawals[index]*debt_share and equity >= withdrawals[index]*equity_share: ## Deduct from both if both are positive
#         debt = (1+ monthly_debt_return)*debt - withdrawals[index]*debt_share
#         equity = (1 + row["Returns"])*equity - withdrawals[index]*equity_share
#     elif equity >= withdrawals[index]:   ## Deduct whole amount from  Equity
#         debt = (1+ monthly_debt_return)*debt
#         equity = (1 + row["Returns"])*equity - withdrawals[index]
#     elif debt >= withdrawals[index]:     ## Dedcut whole amount from Debt
#         debt = (1+ monthly_debt_return)*debt - withdrawals[index]
#         equity = (1 + row["Returns"])*equity 
#     else:
#         debt=0
#         equity=0
#     total_value = equity + debt
#     monthly_portfolio_value.append(total_value)
# monthly_portfolio_value

In [124]:
portfolio_growth_df = pd.DataFrame()
for main_index, main_row in sensex_df.iterrows():
    ## Calculate the portfolio size for person retired each month
    equity = inital_portfolio_size*equity_share
    debt = inital_portfolio_size*debt_share
    current_month_amount = equity + debt
    monthly_portfolio_value = list()
    for index, row in sensex_df.iterrows():
        if main_index < index:
            if debt >= withdrawals[index]*debt_share and equity >= withdrawals[index]*equity_share: ## Deduct from both if both are positive
                debt = (1+ monthly_debt_return)*debt - withdrawals[index]*debt_share
                equity = (1 + row["Returns"])*equity - withdrawals[index]*equity_share
            elif debt < withdrawals[index]:   ## Deduct from equity if debt is less
                debt = (1+ monthly_debt_return)*debt
                equity = (1 + row["Returns"])*equity - withdrawals[index]
            elif equity < withdrawals[index]:     ## Deduct from debt if equity is less
                debt = (1+ monthly_debt_return)*debt - withdrawals[index]
                equity = (1 + row["Returns"])*equity 
            total_value = equity + debt
            monthly_portfolio_value.append(total_value)
        elif main_index == index:
            monthly_portfolio_value.append(equity + debt)
        else:
            monthly_portfolio_value.append(None)
    portfolio_growth_df.insert(main_index, main_row["Month"], monthly_portfolio_value)

In [125]:
portfolio_growth_df

January-1991  February-1991  March-1991  April-1991    May-1991  \
0      100.000000            NaN         NaN         NaN         NaN   
1      116.547792     100.000000         NaN         NaN         NaN   
2      112.407707      96.571291  100.000000         NaN         NaN   
3      116.722331      99.975215  103.600631  100.000000         NaN   
4      121.369417     103.642555  107.479588  103.667954  100.000000   
..            ...            ...         ...         ...         ...   
353    945.020960     471.264013  573.592865  471.631477  373.494152   
354   1015.386449     505.112811  615.324639  505.500472  399.794757   
355   1040.483683     516.350302  629.554297  516.746032  408.167971   
356   1022.899481     506.370134  617.933049  506.762442  399.760774   
357   1086.004079     536.344055  655.059034  536.754758  422.886515   

      June-1991  July-1991  August-1991  September-1991  October-1991  ...  \
0           NaN        NaN          NaN             NaN           NaN  ...   
1           NaN        NaN          NaN             NaN           NaN  ...   
2           NaN        NaN          NaN             NaN           NaN  ...   
3           NaN        NaN          NaN             NaN           NaN  ...   
4           NaN        NaN          NaN             NaN           NaN  ...   
..          ...        ...          ...             ...           ...  ...   
353  440.170794  21.599255  -106.252391     -162.777880   -157.960872  ...   
354  471.605487  20.767821  -116.943432     -177.831494   -172.649498  ...   
355  481.927582  18.843607  -122.609570     -185.153147   -179.832310  ...   
356  472.451801  16.087042  -123.312548     -184.947142   -179.701700  ...   
357  500.235617  14.596637  -133.748284     -199.340881   -193.764240  ...   

     January-2020  February-2020  March-2020  April-2020    May-2020  \
0             NaN            NaN         NaN         NaN         NaN   
1             NaN            NaN         NaN         NaN         NaN   
2             NaN            NaN         NaN         NaN         NaN   
3             NaN            NaN         NaN         NaN         NaN   
4             NaN            NaN         NaN         NaN         NaN   
..            ...            ...         ...         ...         ...   
353     78.273560      84.189888  105.895206   97.780973  103.088552   
354     79.896557      86.228220  109.565803  100.785547  106.461585   
355     79.014713      85.506031  109.465154  100.434123  106.252022   
356     75.901574      82.310333  105.933497   97.045074  102.790170   
357     76.785024      83.570960  108.675392   99.183055  105.262799   

      June-2020   July-2020  August-2020  September-2020  October-2020  
0           NaN         NaN          NaN             NaN           NaN  
1           NaN         NaN          NaN             NaN           NaN  
2           NaN         NaN          NaN             NaN           NaN  
3           NaN         NaN          NaN             NaN           NaN  
4           NaN         NaN          NaN             NaN           NaN  
..          ...         ...          ...             ...           ...  
353  100.000000         NaN          NaN             NaN           NaN  
354  103.094386  100.000000          NaN             NaN           NaN  
355  102.781076   99.590356   100.000000             NaN           NaN  
356   99.381166   96.248319    96.663603      100.000000           NaN  
357  101.601337   98.233758    98.641888      102.158494         100.0  

[358 rows x 358 columns]

In [126]:
file_name = "../data/equity_portfolio.csv"
portfolio_growth_df.to_csv(file_name, sep=',')

In [127]:
100 * (pow((1 + monthly_inflation ), 240)) 

265.3297705144453

In [128]:
fig = px.line(portfolio_growth_df, title='Return from every month - 1991 - 2020')
fig.show()

In [129]:
min_df = pd.DataFrame([portfolio_growth_df.min()])
min_df = min_df.transpose()
min_df.columns = ["minimum"]
min_df

minimum
January-1991    100.000000
February-1991    96.571291
March-1991      100.000000
April-1991      100.000000
May-1991         97.567740
...                    ...
June-2020        99.381166
July-2020        96.248319
August-2020      96.663603
September-2020  100.000000
October-2020    100.000000

[358 rows x 1 columns]

In [130]:
depletion_status = min_df.apply(lambda x: True if x['minimum'] <=0 else False , axis=1)

In [135]:
success = len(depletion_status[depletion_status == True].index)

In [136]:
success/len(depletion_status)

0.7597765363128491

In [137]:
var=5